In [37]:
from kiwipiepy import Kiwi

from langchain_core.output_parsers import StrOutputParser
from langchain_core.runnables import RunnablePassthrough, RunnableLambda
from langchain_community.document_transformers import LongContextReorder

from libs.embeddings import get_embeddings
from libs.retrievers import load_retrievers
from libs.llm import get_llm
from libs.prompt import get_prompt


def kiwi_tokenize(text):
    kiwi = Kiwi()
    return [token.form for token in kiwi.tokenize(text)]


retriever = load_retrievers(get_embeddings())

rag_chain = (
    {
        "context": retriever | RunnableLambda(LongContextReorder().transform_documents),
        "question": RunnablePassthrough(),
    }
    | get_prompt().partial(history=[])
    | get_llm(streaming=False).with_config(configurable={"llm": "gpt_4o"})
    | StrOutputParser()
)

[07/12/24 00:07:27] INFO     [SentenceTransformer.py:197] >> Load pretrained             ]8;id=770733;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/sentence_transformers/SentenceTransformer.py\SentenceTransformer.py]8;;\:]8;id=848554;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/sentence_transformers/SentenceTransformer.py#197\197]8;;\
                             SentenceTransformer: BAAI/bge-m3                                                      

In [30]:
import pandas as pd

qa_df = pd.read_parquet("evaluation_data/qa.parquet", engine="pyarrow")
qa_df.head()

retrieval_gt  \
0  [[fff45aa2-fc19-476e-83df-fc4fe02ac113]]   
1  [[9a5ceb80-6113-41c2-ae31-8c9298150153]]   
2  [[3548ce6b-c9de-47e5-a007-19d3eff1fe34]]   
3  [[f27b8a4d-a9a2-4d57-a4c6-fe9f45e286f8]]   
4  [[505e9c85-2c82-480e-9219-85b1c28e7ea7]]   

                                    qid  \
0  92c99d41-de88-4eba-85ef-9867c5d6e686   
1  c20df26b-8010-4c88-88cf-741af73f3ef1   
2  a0f28fc3-de71-4b13-bbdf-6b4458bb1735   
3  a2da6f15-3237-4da0-b592-1a971e502778   
4  7756a8a0-203d-4b3e-a350-ff6c92771714   

                                               query  \
0  아버지가 돌아가신 후, 아버지가 가진 노인복지시설 보증금에 대해 저가 아닌 형이 받...   
1  저는 3년 동안 일하다가 퇴사했는데, 퇴직금 계산 시 근무 기간을 어떻게 계산해야 ...   
2  회사 주식 전부를 소유한 외국 법인이 다른 자회사에 주식을 현물출자하고, 이후 원래...   
3  이웃집의 반려견이 매일 밤 매우 크게 짖어서 잠을 설쳐요. 이에 대해 법적으로 대응...   
4  저는 2년 동안 근무한 직장에서 해고되었습니다. 그러나 회사 측에서는 저에게 어떤 ...   

                                       generation_gt  
0  [이 사건은 귀하와 관련된 실제 사례가 아니지만, 유사한 판례인 219733,부당이...  
1  [제가 이해한 바로는, 퇴직금 계산 시 근무 기간을 어떻게 계산해야 하는지에 대한 ...  
2  [법률 판례와 관련된 질문입니다. 관련 판례는 '230909, 법인세징수처분등취소청...  
3  [이웃의 반려견으로 인한 소음 피해와 관련된 판례 중 하나는 2018년 서울고등법원...  
4  [근로기준법은 사용자가 근로자를 해고할 때 30일 전에 예고를 하도록 규정하고 있습...

In [32]:
qa_df = qa_df[["query", "generation_gt"]]
qa_df.columns = ["question", "ground_truth"]
qa_df.head()

question  \
0  아버지가 돌아가신 후, 아버지가 가진 노인복지시설 보증금에 대해 저가 아닌 형이 받...   
1  저는 3년 동안 일하다가 퇴사했는데, 퇴직금 계산 시 근무 기간을 어떻게 계산해야 ...   
2  회사 주식 전부를 소유한 외국 법인이 다른 자회사에 주식을 현물출자하고, 이후 원래...   
3  이웃집의 반려견이 매일 밤 매우 크게 짖어서 잠을 설쳐요. 이에 대해 법적으로 대응...   
4  저는 2년 동안 근무한 직장에서 해고되었습니다. 그러나 회사 측에서는 저에게 어떤 ...   

                                        ground_truth  
0  [이 사건은 귀하와 관련된 실제 사례가 아니지만, 유사한 판례인 219733,부당이...  
1  [제가 이해한 바로는, 퇴직금 계산 시 근무 기간을 어떻게 계산해야 하는지에 대한 ...  
2  [법률 판례와 관련된 질문입니다. 관련 판례는 '230909, 법인세징수처분등취소청...  
3  [이웃의 반려견으로 인한 소음 피해와 관련된 판례 중 하나는 2018년 서울고등법원...  
4  [근로기준법은 사용자가 근로자를 해고할 때 30일 전에 예고를 하도록 규정하고 있습...

In [33]:
qa_df["ground_truth"] = qa_df["ground_truth"].apply(lambda x: x[0])
qa_df["ground_truth"]

0     이 사건은 귀하와 관련된 실제 사례가 아니지만, 유사한 판례인 219733,부당이득...
1     제가 이해한 바로는, 퇴직금 계산 시 근무 기간을 어떻게 계산해야 하는지에 대한 판...
2     법률 판례와 관련된 질문입니다. 관련 판례는 '230909, 법인세징수처분등취소청구...
3     이웃의 반려견으로 인한 소음 피해와 관련된 판례 중 하나는 2018년 서울고등법원 ...
4     근로기준법은 사용자가 근로자를 해고할 때 30일 전에 예고를 하도록 규정하고 있습니...
5     공법 제30조에 따라, 공인중개사가 확인 및 설명 의무를 위반하여 임차인에게 재산상...
6     예, 지역주택조합 가입계약을 해제하고 계약금을 반환받을 수 있는 경우가 있습니다. ...
7     예, 저희는 판례와 관련된 내용을 알려드리고 있습니다. 성적 괴롭힘과 보복에 대한 ...
8     네, 유사한 판례가 있습니다. "238455,요양급여불승인처분취소청구,2020두54...
9     이 사건에 관련된 판례를 소개해 드리겠습니다: "상속 한정승인자의 예금, 상속재산 ...
10    주어진 판례는 공직자가 직무와 관련된 공식 행사에서 주최 측으로부터 무료로 숙박 서...
11    [1] 공직선거법 제60조의3 제1항 제5호에 따라 예비후보자에게 허용되는 선거운동...
12    준강제추행죄에서 심신상실이란 성적 행위에 대한 정상적인 판단능력이 없는 상태를 의미...
13    검사가 증거로 제출한 CD에 복제된 동영상 파일은 경찰이 피고인에게 참여의 기회를 ...
14    지인 간의 금전 거래에서 발생한 이자에 대한 판례는 상황에 따라 다를 수 있습니다....
15    240649, 임금등청구의소[부당하게 해고된 후 원직이 아닌 업무에 복직된 근로자가...
16    응급 환자의 의료 처치와 관련된 법률 판례는 다양하며, 의료진의 책임은 상황에 따라...
17    사기죄와 관련된 유사한 판례로는 Daum 등의 사건(2003도382)이 있습

In [39]:
qa_df["answer"] = qa_df["question"].apply(lambda x: rag_chain.invoke(x))
qa_df["contexts"] = qa_df["question"].apply(
    lambda x: [d.page_content for d in retriever.get_relevant_documents(x)]
)
qa_df.head()

[07/12/24 00:17:48] INFO     [_client.py:1026] >> HTTP Request: POST                                ]8;id=34084;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/httpx/_client.py\_client.py]8;;\:]8;id=477818;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/httpx/_client.py#1026\1026]8;;\
                             https://api.cohere.com/v1/rerank "HTTP/1.1 200 OK"                                    

[07/12/24 00:18:00] INFO     [_client.py:1026] >> HTTP Request: POST                                ]8;id=478426;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/httpx/_client.py\_client.py]8;;\:]8;id=199969;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/httpx/_client.py#1026\1026]8;;\
                             https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"                          

[07/12/24 00:18:21] INFO     [_client.py:1026] >> HTTP Request: POST                                ]8;id=132269;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/httpx/_client.py\_client.py]8;;\:]8;id=184383;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/httpx/_client.py#1026\1026]8;;\
                             https://api.cohere.com/v1/rerank "HTTP/1.1 200 OK"                                    

[07/12/24 00:18:38] INFO     [_client.py:1026] >> HTTP Request: POST                                ]8;id=560981;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/httpx/_client.py\_client.py]8;;\:]8;id=562527;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/httpx/_client.py#1026\1026]8;;\
                             https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"                          

[07/12/24 00:19:00] INFO     [_client.py:1026] >> HTTP Request: POST                                ]8;id=532456;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/httpx/_client.py\_client.py]8;;\:]8;id=41854;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/httpx/_client.py#1026\1026]8;;\
                             https://api.cohere.com/v1/rerank "HTTP/1.1 200 OK"                                    

...

[07/12/24 00:35:28] INFO     [_client.py:1026] >> HTTP Request: POST                                ]8;id=415017;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/httpx/_client.py\_client.py]8;;\:]8;id=822620;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/httpx/_client.py#1026\1026]8;;\
                             https://api.cohere.com/v1/rerank "HTTP/1.1 200 OK"                                    

[07/12/24 00:35:44] INFO     [_client.py:1026] >> HTTP Request: POST                                ]8;id=268337;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/httpx/_client.py\_client.py]8;;\:]8;id=505576;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/httpx/_client.py#1026\1026]8;;\
                             https://api.cohere.com/v1/rerank "HTTP/1.1 200 OK"                                    

[07/12/24 00:36:00] INFO     [_client.py:1026] >> HTTP Request: POST                                ]8;id=556299;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/httpx/_client.py\_client.py]8;;\:]8;id=241493;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/httpx/_client.py#1026\1026]8;;\
                             https://api.cohere.com/v1/rerank "HTTP/1.1 200 OK"                                    

[07/12/24 00:36:16] INFO     [_client.py:1026] >> HTTP Request: POST                                ]8;id=589335;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/httpx/_client.py\_client.py]8;;\:]8;id=641100;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/httpx/_client.py#1026\1026]8;;\
                             https://api.cohere.com/v1/rerank "HTTP/1.1 200 OK"                                    

question  \
0  아버지가 돌아가신 후, 아버지가 가진 노인복지시설 보증금에 대해 저가 아닌 형이 받...   
1  저는 3년 동안 일하다가 퇴사했는데, 퇴직금 계산 시 근무 기간을 어떻게 계산해야 ...   
2  회사 주식 전부를 소유한 외국 법인이 다른 자회사에 주식을 현물출자하고, 이후 원래...   
3  이웃집의 반려견이 매일 밤 매우 크게 짖어서 잠을 설쳐요. 이에 대해 법적으로 대응...   
4  저는 2년 동안 근무한 직장에서 해고되었습니다. 그러나 회사 측에서는 저에게 어떤 ...   

                                        ground_truth  \
0  [이 사건은 귀하와 관련된 실제 사례가 아니지만, 유사한 판례인 219733,부당이...   
1  [제가 이해한 바로는, 퇴직금 계산 시 근무 기간을 어떻게 계산해야 하는지에 대한 ...   
2  [법률 판례와 관련된 질문입니다. 관련 판례는 '230909, 법인세징수처분등취소청...   
3  [이웃의 반려견으로 인한 소음 피해와 관련된 판례 중 하나는 2018년 서울고등법원...   
4  [근로기준법은 사용자가 근로자를 해고할 때 30일 전에 예고를 하도록 규정하고 있습...   

                                              answer  \
0  안타깝게도 주어진 문서에서 귀하의 질문에 대한 직접적인 답변을 찾지 못했습니다. 하...   
1  [사건 1]\n- 사건 이름: 퇴직금\n- 간단한 설명: 이 사건에서는 근로자가 퇴...   
2  안녕하세요. 질문해주신 상황에 대해 비슷한 판례를 찾아보았습니다. 아래에 세 가지 ...   
3  안타깝게도 주어진 문서에서 귀하의 질문에 대한 직접적인 답변을 찾지 못했습니다. 하...   
4  안타깝게도 주어진 문서에서 귀하의 질문에 대한 직접적인 답변을 찾지 못했습니다. 하...   

                                            contexts  
0  [208930,부당이득반환,4290민상290,1957.07.25,대법원,민사,400...  
1  [라. 정당한 퇴직금의 계산(1) 매월 지급받은 정기급여는 급여계산기간의 중도에 퇴...  
2  [230909,법인세징수처분등취소청구,2017두31347,2022.03.31,대법원...  
3  [238929,스토킹범죄의처벌등에관한법률위반[수개월간 반복하여 고의로 소음을 발생시...  
4  [,[원고, 상고인] 원고 (소송대리인 법무법인 어울림 담당변호사 구은미 외 2인)...

In [40]:
from datasets import Dataset

dataset = Dataset.from_pandas(qa_df)
dataset[0]

{'question': '아버지가 돌아가신 후, 아버지가 가진 노인복지시설 보증금에 대해 저가 아닌 형이 받게 된 경우, 이에 대해 제가 이의를 제기할 수 있을까요? 이와 관련된 판례가 있을까요?',
 'ground_truth': ['이 사건은 귀하와 관련된 실제 사례가 아니지만, 유사한 판례인 219733,부당이득금반환,2021다271183,2022.01.14,대법원,민사,400101.0,판결,선고 사건을 참고할 수 있습니다. 이 판결은 노인복지시설 입소자가 자신의 사망 시 반환금 수취인으로 제3자를 지정한 계약에 대한 것으로, 수취인이 계약서에 기명날인을 하여 수익의 의사표시를 한 경우, 수취인은 계약에 따른 수익자로서의 권리와 이행을 받을 수 있다고 판결한 사례입니다. 이 판결은 구체적인 사실관계에 따라 다를 수 있으므로, 귀하의 상황에 적용하기 위해서는 법률 전문가와 상담하는 것이 좋습니다.'],
 'answer': '안타깝게도 주어진 문서에서 귀하의 질문에 대한 직접적인 답변을 찾지 못했습니다. 하지만 이와 관련하여 다음과 같은 정보를 제공해 드릴 수 있습니다:\n\n1. 일반적인 법률 원칙:\n   - 상속: 아버지가 돌아가신 후, 아버지의 재산은 상속인들에게 상속됩니다. 상속인들은 법에 따라 상속분을 나누게 됩니다. 만약 상속분에 대해 이의가 있다면, 법원에 상속재산분할심판을 청구할 수 있습니다.\n   - 유언: 아버지가 유언을 남기셨다면, 유언에 따라 재산이 분배됩니다. 유언이 법적으로 유효한지 여부는 법원에서 판단할 수 있습니다.\n\n2. 비슷한 사례:\n   - [사건 1]\n     - 사건 이름: 인지등\n     - 간단한 설명: 미성년자가 부양의무자인 친권자에게 부양료를 청구한 사건입니다.\n     - 질문자의 상황과 비슷한 점: 상속과 관련된 법적 권리를 주장하는 점에서 유사합니다.\n     - 판결 결과: 미성년자는 부양의무자인 친권자에게 직접 부양료를 청구할 수 있다고 판결되었습니다.\n     - 출처: [154671, 

In [41]:
dataset.save_to_disk("evaluation_data/dataset")

Saving the dataset (0/1 shards):   0%|          | 0/20 [00:00<?, ? examples/s]

In [63]:
dataset = Dataset.load_from_disk("evaluation_data/dataset")
dataset[0]

{'question': '아버지가 돌아가신 후, 아버지가 가진 노인복지시설 보증금에 대해 저가 아닌 형이 받게 된 경우, 이에 대해 제가 이의를 제기할 수 있을까요? 이와 관련된 판례가 있을까요?',
 'ground_truth': ['이 사건은 귀하와 관련된 실제 사례가 아니지만, 유사한 판례인 219733,부당이득금반환,2021다271183,2022.01.14,대법원,민사,400101.0,판결,선고 사건을 참고할 수 있습니다. 이 판결은 노인복지시설 입소자가 자신의 사망 시 반환금 수취인으로 제3자를 지정한 계약에 대한 것으로, 수취인이 계약서에 기명날인을 하여 수익의 의사표시를 한 경우, 수취인은 계약에 따른 수익자로서의 권리와 이행을 받을 수 있다고 판결한 사례입니다. 이 판결은 구체적인 사실관계에 따라 다를 수 있으므로, 귀하의 상황에 적용하기 위해서는 법률 전문가와 상담하는 것이 좋습니다.'],
 'answer': '안타깝게도 주어진 문서에서 귀하의 질문에 대한 직접적인 답변을 찾지 못했습니다. 하지만 이와 관련하여 다음과 같은 정보를 제공해 드릴 수 있습니다:\n\n1. 일반적인 법률 원칙:\n   - 상속: 아버지가 돌아가신 후, 아버지의 재산은 상속인들에게 상속됩니다. 상속인들은 법에 따라 상속분을 나누게 됩니다. 만약 상속분에 대해 이의가 있다면, 법원에 상속재산분할심판을 청구할 수 있습니다.\n   - 유언: 아버지가 유언을 남기셨다면, 유언에 따라 재산이 분배됩니다. 유언이 법적으로 유효한지 여부는 법원에서 판단할 수 있습니다.\n\n2. 비슷한 사례:\n   - [사건 1]\n     - 사건 이름: 인지등\n     - 간단한 설명: 미성년자가 부양의무자인 친권자에게 부양료를 청구한 사건입니다.\n     - 질문자의 상황과 비슷한 점: 상속과 관련된 법적 권리를 주장하는 점에서 유사합니다.\n     - 판결 결과: 미성년자는 부양의무자인 친권자에게 직접 부양료를 청구할 수 있다고 판결되었습니다.\n     - 출처: [154671, 

In [64]:
# fix ground_truth
dataset = dataset.map(lambda x: {"ground_truth": x["ground_truth"][0]})
dataset[0]

{'question': '아버지가 돌아가신 후, 아버지가 가진 노인복지시설 보증금에 대해 저가 아닌 형이 받게 된 경우, 이에 대해 제가 이의를 제기할 수 있을까요? 이와 관련된 판례가 있을까요?',
 'ground_truth': '이 사건은 귀하와 관련된 실제 사례가 아니지만, 유사한 판례인 219733,부당이득금반환,2021다271183,2022.01.14,대법원,민사,400101.0,판결,선고 사건을 참고할 수 있습니다. 이 판결은 노인복지시설 입소자가 자신의 사망 시 반환금 수취인으로 제3자를 지정한 계약에 대한 것으로, 수취인이 계약서에 기명날인을 하여 수익의 의사표시를 한 경우, 수취인은 계약에 따른 수익자로서의 권리와 이행을 받을 수 있다고 판결한 사례입니다. 이 판결은 구체적인 사실관계에 따라 다를 수 있으므로, 귀하의 상황에 적용하기 위해서는 법률 전문가와 상담하는 것이 좋습니다.',
 'answer': '안타깝게도 주어진 문서에서 귀하의 질문에 대한 직접적인 답변을 찾지 못했습니다. 하지만 이와 관련하여 다음과 같은 정보를 제공해 드릴 수 있습니다:\n\n1. 일반적인 법률 원칙:\n   - 상속: 아버지가 돌아가신 후, 아버지의 재산은 상속인들에게 상속됩니다. 상속인들은 법에 따라 상속분을 나누게 됩니다. 만약 상속분에 대해 이의가 있다면, 법원에 상속재산분할심판을 청구할 수 있습니다.\n   - 유언: 아버지가 유언을 남기셨다면, 유언에 따라 재산이 분배됩니다. 유언이 법적으로 유효한지 여부는 법원에서 판단할 수 있습니다.\n\n2. 비슷한 사례:\n   - [사건 1]\n     - 사건 이름: 인지등\n     - 간단한 설명: 미성년자가 부양의무자인 친권자에게 부양료를 청구한 사건입니다.\n     - 질문자의 상황과 비슷한 점: 상속과 관련된 법적 권리를 주장하는 점에서 유사합니다.\n     - 판결 결과: 미성년자는 부양의무자인 친권자에게 직접 부양료를 청구할 수 있다고 판결되었습니다.\n     - 출처: [154671, 인지

In [78]:
from ragas.metrics import (
    faithfulness,
    answer_relevancy,
    context_recall,
    context_precision,
)
from ragas.metrics.critique import harmfulness
from ragas import evaluate

from langchain_openai import ChatOpenAI
from libs.embeddings import get_embeddings

In [48]:
embeddings = get_embeddings()

[07/12/24 00:40:11] INFO     [SentenceTransformer.py:197] >> Load pretrained             ]8;id=631938;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/sentence_transformers/SentenceTransformer.py\SentenceTransformer.py]8;;\:]8;id=578432;file:///Users/anpigon/Library/Caches/pypoetry/virtualenvs/law-bot-C3zMZhS7-py3.11/lib/python3.11/site-packages/sentence_transformers/SentenceTransformer.py#197\197]8;;\
                             SentenceTransformer: BAAI/bge-m3                                                      

In [75]:
from ragas.llms import LangchainLLMWrapper

llm = ChatOpenAI(model="gpt-4o", temperature=0.0)
langchain_llm = LangchainLLMWrapper(llm)

In [76]:
langchain_llm.set_run_config

<bound method LangchainLLMWrapper.set_run_config of LangchainLLMWrapper(run_config=RunConfig(timeout=60, max_retries=10, max_wait=60, max_workers=16, thread_timeout=80.0, exception_types=<class 'openai.RateLimitError'>, log_tenacity=False))>

In [79]:
result = evaluate(
    dataset,
    metrics=[
        faithfulness,
        answer_relevancy,
        context_recall,
        context_precision,
        harmfulness,
    ],
    llm=langchain_llm,
    embeddings=embeddings,
    raise_exceptions=False,
)

result

AttributeError: 'ChatOpenAI' object has no attribute 'set_run_config'